# 0 : Cosa c'è in questo notebook
Scaricamanto ed utilizzo modelli di Natural Language Processing da huggingface.com per fare un po di esperimenti ed esempi con dati testuali per il progetto __geografia__.

In particolare si esplorano un po di metodi e strumenti per la comprensione e annotazione dei testi, sfruttando modelli già allenati su task che ci posssono interessare come ad esempio :
- __Mask-Filling__ (con huggingface transformer): predice un token mancante in una frase
- __Zero-Shot classification__ (con huggingface transformer): classifica una frase rispetto a delle classi variabili (utile per topic analysis, sentiment retrival e menate generiche)
- __Pos-Tagging__ (con la libreria spacy) : analisi grammaticale e sintattica del testo

#### 0.1 Transformer Models da hugging face
I modelli pre-allenati sono stati sottoposti ad estensivi training con tantissimi dati, in genere macinati per giorni. i task non-supervisionati tipici utilizzati per l'allenamento sono in genere:
- next sentence prediction ( prendi un paragrafo, lo splitti sulla base del carattere '.' ed usi la prima frase come dato e la seconda come label da predirre)
- fill-mask: predirre la parola mancante di una frase ( nel training si prendono frasi complete e si maschera un termine a random per frase)

Accanto a questi task usati per allenare la struttura della rete neurale (aka "il grosso" dei nodi profondi), i modelli di huggingface possono essere già "fine-tunati" rispetto ad ulteriori downstream task (tipo sentiment analysis o zero shot) e quindi utilizzabili direttamente. per alcune coppie di modelli-task invece è necessario un ulteriore sessione di fine-tuning con un dataset rilevante per il task d'interesse.
Qua c'è una lista delle tipologie di task piu comuni:
https://huggingface.co/tasks
 
Infine un altra differenza sostanziale che ci interessa è se il modello sia:
- monolingua
- multilingua

i modelli considerati per questo girovagare sono:
- il modello __dbmdz/bert-base-italian-cased__ è piu leggero e solo in italiano, ma di task ready-to-go disponibili c'è solo fill-mask e pos-tag
- il modello __facebook/bart-large-mnli__ è molto pesante, ma è multilingua ed ha implementato lo zero-shot-classification
- il modello __bert-base-cased__ solo inglese ma con praticamente tutti i downstream task già pronti all'utilizzo

#### 0.2 Spacy Library
https://spacy.io/
libreria python piu semplice ed efficiente rispetto ai modelli transformer di hugging face, ma meno versatile per quantità di task possibili. ottima per pulire testi e tokenization (preprocessing), molto buono il pos-tagging



In [1]:
from transformers import AutoModel, AutoTokenizer 
from transformers import pipeline
multilingual_model_name = "facebook/bart-large-mnli" # 1.5 GB
italian_model_name = "dbmdz/bert-base-italian-cased" # 422 MB
alltask_model_name = "bert-base-cased" 

## Download model and configuration from huggingface.co and cache. 
#muli_tokenizer = AutoTokenizer.from_pretrained(multilingual_model_name)
#muli_model = AutoModel.from_pretrained(multilingual_model_name)


/home/agropunx/anaconda3/envs/geografia/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2022-07-06 20:22:23.485088: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-07-06 20:22:23.485116: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


## 1 : Fill-Mask task example

In [2]:
fill = pipeline('fill-mask',model=italian_model_name)
masked_sentence = 'Umberto Eco è [MASK] un grande scrittore'
fill(masked_sentence)

Some weights of the model checkpoint at dbmdz/bert-base-italian-cased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


[{'score': 0.9144049286842346,
  'token': 482,
  'token_str': 'stato',
  'sequence': 'Umberto Eco è stato un grande scrittore'},
 {'score': 0.025699790567159653,
  'token': 5801,
  'token_str': 'diventato',
  'sequence': 'Umberto Eco è diventato un grande scrittore'},
 {'score': 0.022715440019965172,
  'token': 409,
  'token_str': 'anche',
  'sequence': 'Umberto Eco è anche un grande scrittore'},
 {'score': 0.006274252198636532,
  'token': 1402,
  'token_str': 'oggi',
  'sequence': 'Umberto Eco è oggi un grande scrittore'},
 {'score': 0.004773850552737713,
  'token': 14743,
  'token_str': 'divenuto',
  'sequence': 'Umberto Eco è divenuto un grande scrittore'}]

In [3]:
masked_sentence = 'a che ora ci [MASK]?'
fill(masked_sentence)

[{'score': 0.1162119209766388,
  'token': 7607,
  'token_str': 'troviamo',
  'sequence': 'a che ora ci troviamo?'},
 {'score': 0.06763438880443573,
  'token': 17567,
  'token_str': 'aspettiamo',
  'sequence': 'a che ora ci aspettiamo?'},
 {'score': 0.06530702114105225,
  'token': 1303,
  'token_str': 'sarà',
  'sequence': 'a che ora ci sarà?'},
 {'score': 0.05703262239694595,
  'token': 4238,
  'token_str': 'vediamo',
  'sequence': 'a che ora ci vediamo?'},
 {'score': 0.05302278324961662,
  'token': 17387,
  'token_str': 'vedete',
  'sequence': 'a che ora ci vedete?'}]

In [4]:
masked_sentence = 'a che [MASK] ci troviamo?'
fill(masked_sentence)

[{'score': 0.36587169766426086,
  'token': 510,
  'token_str': 'cosa',
  'sequence': 'a che cosa ci troviamo?'},
 {'score': 0.046960778534412384,
  'token': 739,
  'token_str': 'modo',
  'sequence': 'a che modo ci troviamo?'},
 {'score': 0.04375715181231499,
  'token': 212,
  'token_str': 'non',
  'sequence': 'a che non ci troviamo?'},
 {'score': 0.023330960422754288,
  'token': 1302,
  'token_str': 'livello',
  'sequence': 'a che livello ci troviamo?'},
 {'score': 0.02314317226409912,
  'token': 1711,
  'token_str': 'condizioni',
  'sequence': 'a che condizioni ci troviamo?'}]

## 2 : Zero-Shot classification task example

uso modello multilingua ( unico disponibile su huggingface in grado di performare l'inferenza zero-shot in italiano)
 
link generico in italiano sullo __zero-shot__ learning e inference: https://zephyrnet.com/it/Zero-shot-learning-puoi-classificare-un-oggetto-senza-vederlo-prima/

In [5]:
zs = pipeline("zero-shot-classification",model=italian_model_name)

Some weights of the model checkpoint at dbmdz/bert-base-italian-cased were not used when initializing BertForSequenceClassification: ['cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model c

In [ ]:
zs('che merda di giornata', candidate_labels=['positivo','negativo'],hypothesis_template='questa frase ha un tono {}',) #multiclass

In [ ]:
zs(sequences='dove vai stasera?',hypothesis_template='questa frase è una {}',candidate_labels=['affermazione','domanda'])

In [ ]:
zs(sequences='where are you going?',hypothesis_template='this phrase is a {}',candidate_labels=['question','affirmation'])

In [ ]:
zs(sequences='Voglio uscire con voi stasera, ma devo pulire casa prima',candidate_labels=['dubbio','invito','carro','positivo','negativo'], multiclass=True)

In [8]:
#https://www.google.it/search?q=thayer+mood+plane+italia&biw=1528&bih=788&tbm=isch&source=iu&ictx=1&vet=1&fir=idr_CWra3dTA3M%252C3vr2PPAMir9TdM%252C_%253BEhLHcfw0fkhWHM%252CEh6xJHBGzk4cMM%252C_%253BaP-KPSMboAJg2M%252CnleMstLur1huUM%252C_%253BxHGASYvcnwBR5M%252CrZKJnx3na11TtM%252C_%253Bl2JjpwGxrk9aOM%252CEh6xJHBGzk4cMM%252C_%253BGC1du1ZkYglw-M%252Co4brRqZQk5p8CM%252C_%253BO8E8kjpRcFlMWM%252CnleMstLur1huUM%252C_%253BoYYMLq4zR-JFeM%252Co4brRqZQk5p8CM%252C_%253B1CIJmqw2RNg0VM%252C5o_XDTGFr1iuXM%252C_%253BaDO14J7XISRjIM%252CEh6xJHBGzk4cMM%252C_&usg=AI4_-kSIgRNOu3F0-x0YYMbNCEIyLXfEzg&sa=X&ved=2ahUKEwiyqNDN_cD3AhVc7rsIHWi3CFYQ9QF6BAghEAE#imgrc=EhLHcfw0fkhWHM
moods=['fastidio','rabbia','sconforto','tristezza','noia','pace','relax','calma','felicità','gioia','indifferenza','interesse','dubbio','eccitazione']
zs(sequences='Sono felice di uscire con voi stasera',candidate_labels=moods)

{'sequence': 'Sono felice di uscire con voi stasera',
 'labels': ['relax',
  'pace',
  'indifferenza',
  'interesse',
  'fastidio',
  'dubbio',
  'noia',
  'rabbia',
  'sconforto',
  'calma',
  'tristezza',
  'eccitazione',
  'gioia',
  'felicità'],
 'scores': [0.07741541415452957,
  0.07665539532899857,
  0.0763017013669014,
  0.07597608864307404,
  0.07575443387031555,
  0.07570748031139374,
  0.0756787359714508,
  0.07537700980901718,
  0.07522716373205185,
  0.07521089166402817,
  0.07490663230419159,
  0.07221430540084839,
  0.07031130790710449,
  0.02326352894306183]}

In [9]:
sentenza = 'ti ammazzo'
zs(sequences=sentenza,candidate_labels=moods)

{'sequence': 'ti ammazzo',
 'labels': ['noia',
  'eccitazione',
  'pace',
  'dubbio',
  'gioia',
  'rabbia',
  'indifferenza',
  'tristezza',
  'sconforto',
  'felicità',
  'fastidio',
  'calma',
  'relax',
  'interesse'],
 'scores': [0.07284864038228989,
  0.07268563657999039,
  0.07168520241975784,
  0.07163083553314209,
  0.07157977670431137,
  0.07146152853965759,
  0.07145626842975616,
  0.07143832743167877,
  0.07120247930288315,
  0.07110902667045593,
  0.07106047123670578,
  0.07105831056833267,
  0.07071790099143982,
  0.07006552070379257]}

In [13]:
sentenza = 'non capisco perchè te la prendi con me, ti ho già regalato tutte le mi capre, non posso darti anche il bue'
zs(sequences=sentenza,candidate_labels=moods, multiclass=True)

{'sequence': 'non capisco perchè te la prendi con me, ti ho già regalato tutte le mi capre, non posso darti anche il bue',
 'labels': ['eccitazione',
  'indifferenza',
  'gioia',
  'relax',
  'felicità',
  'dubbio',
  'tristezza',
  'fastidio',
  'pace',
  'rabbia',
  'noia',
  'interesse',
  'sconforto',
  'calma'],
 'scores': [0.07354768365621567,
  0.07300304621458054,
  0.07294241338968277,
  0.07219138741493225,
  0.07172053307294846,
  0.07144749164581299,
  0.07143128663301468,
  0.07104679197072983,
  0.07093875855207443,
  0.07085791230201721,
  0.0706729143857956,
  0.07063259184360504,
  0.07041624188423157,
  0.06915094703435898]}

In [14]:
zs(sequences='le tue orecchie sono bruttissime, non uscirò mai con te',candidate_labels=['estetica','logica','attualità','cotillons'], multiclass=True)

{'sequence': 'le tue orecchie sono bruttissime, non uscirò mai con te',
 'labels': ['logica', 'attualità', 'cotillons', 'estetica'],
 'scores': [0.2509896755218506,
  0.25027403235435486,
  0.24949680268764496,
  0.2492394745349884]}

## 3 : POS-TAG task example

Positional tagging, task già noto alla maggior parte delle persone aventi la terza elementare come __analisi grammaticale__
Nell'analisi grammaticale italiana ogni parola può appartenere ad una delle nove categorie lessicali dell'italiano, cinque variabili: articolo, aggettivo, sostantivo o nome, pronome, verbo, e quattro invariabili: avverbio, preposizione, congiunzione, interiezione o esclamazione. 

In [15]:
import spacy
from spacy.lang.it.examples import sentences 

try:
    nlp = spacy.load("it_core_news_lg")
except:
    !python -m spacy download it_core_news_lg
    nlp = spacy.load("it_core_news_lg")
doc = nlp(sentences[2])
print('testo originale ---> ',doc.text)
print('\n*** Pos-Tagging')
print('WORD', ' '*(10-len('word')), 'POS-TAG',' '*(10-len('POS-TAG')), 'SYNTACTIC DEP')
print('-------------------------------------')
for token in doc:
    print(token.text,' '*(10-len(token.text)), token.pos_,' '*(10-len(token.pos_)), token.dep_ )

print('\n*** Analisi Entità specifiche nel testo:')    
print('ENTITY NAME',' '*(20-len('ENTITY NAME')), 'LABEL')
print('-------------------------------------')
for ent in doc.ents:
    print(ent.text ,' '*(20-len(ent.text)), ent.label_)

testo originale --->  San Francisco prevede di bandire i robot di consegna porta a porta

*** Pos-Tagging
WORD        POS-TAG     SYNTACTIC DEP
-------------------------------------
San         PROPN       nsubj
Francisco   PROPN       flat:name
prevede     VERB        ROOT
di          ADP         mark
bandire     VERB        xcomp
i           DET         det
robot       NOUN        obj
di          ADP         case
consegna    NOUN        nmod
porta       VERB        advcl
a           ADP         case
porta       NOUN        obl

*** Analisi Entità specifiche nel testo:
ENTITY NAME           LABEL
-------------------------------------
San Francisco         LOC


In [16]:
doc = nlp(sentences[3])
print('testo originale ---> ',doc.text)
print('\n*** Pos-Tagging')
print('WORD', ' '*(10-len('word')), 'POS-TAG',' '*(10-len('POS-TAG')), 'SYNTACTIC DEP')
print('-------------------------------------')
for token in doc:
    print(token.text,' '*(10-len(token.text)), token.pos_,' '*(10-len(token.pos_)), token.dep_ )

print('\n*** Analisi Entità specifiche nel testo:')    
print('ENTITY NAME',' '*(20-len('ENTITY NAME')), 'LABEL')
print('-------------------------------------')
for ent in doc.ents:
    print(ent.text ,' '*(20-len(ent.text)), ent.label_)

testo originale --->  Londra è una grande città del Regno Unito.

*** Pos-Tagging
WORD        POS-TAG     SYNTACTIC DEP
-------------------------------------
Londra      PROPN       nsubj
è           AUX         cop
una         DET         det
grande      ADJ         amod
città       NOUN        ROOT
del         ADP         case
Regno       PROPN       nmod
Unito       PROPN       flat:name
.           PUNCT       punct

*** Analisi Entità specifiche nel testo:
ENTITY NAME           LABEL
-------------------------------------
Londra                LOC
Regno Unito           LOC


In [17]:
doc = nlp(sentenza.replace('me','Giacomo').replace('mi','sue').replace('ho','ha').replace('posso','può'))
print('testo originale ---> ',doc.text)
print('\n*** Pos-Tagging')
print('WORD', ' '*(10-len('word')), 'POS-TAG',' '*(10-len('POS-TAG')), 'SYNTACTIC DEP')
print('-------------------------------------')
for token in doc:
    print(token.text,' '*(10-len(token.text)), token.pos_,' '*(10-len(token.pos_)), token.dep_ )

print('\n*** Analisi Entità specifiche nel testo:')    
print('ENTITY NAME',' '*(20-len('ENTITY NAME')), 'LABEL')
print('-------------------------------------')
for ent in doc.ents:
    print(ent.text ,' '*(20-len(ent.text)), ent.label_)

testo originale --->  non capisco perchè te la prendi con Giacomo, ti ha già regalato tutte le sue capre, non può darti anche il bue

*** Pos-Tagging
WORD        POS-TAG     SYNTACTIC DEP
-------------------------------------
non         ADV         advmod
capisco     VERB        ROOT
perchè      SCONJ       mark
te          PRON        expl
la          PRON        obj
prendi      VERB        ccomp
con         ADP         case
Giacomo     PROPN       obl
,           PUNCT       punct
ti          PRON        iobj
ha          AUX         aux
già         ADV         advmod
regalato    VERB        conj
tutte       DET         det:predet
le          DET         det
sue         DET         det:poss
capre       NOUN        obj
,           PUNCT       punct
non         ADV         advmod
può         AUX         aux
darti       VERB        conj
anche       ADV         advmod
il          DET         det
bue         NOUN        obj

*** Analisi Entità specifiche nel testo:
ENTITY NAME           L